# Data Munging

In [1]:
import pandas as pd
import numpy as np

# header=0 doens't work, header=None simply inserts intergers as column names
df_raw = pd.read_csv(r"./ticdata2000.txt", sep='\t', header=None, low_memory=False)

In [2]:
def display_all(df):
    with pd.option_context("display.max_rows", 1000, "display.max_columns", 1000): 
        display(df)

In [3]:
### DEPRECATED BY THE FOLLOWING CELL ###

# def get_item_description(start_row, end_row, from_nth_field_onward):
#     """
#     RETURN: A list of extracted item names
#     start_row: Starting row number of dictionary.txt
#     end_row: Ending row number of dictionary.txt
#     from_nth_field_onward: Take out a n-th field, delimited by space, and further to the right
#     """
    
#     # Thought of returning a ndarray but a "DeprecationWarning: 
#     #  "using a non-integer array as obj in delete will result in an error in the future"
#     import subprocess
    
#     unix_shell_command = 'awk \'NR>={0}&&NR<={1}\' "./dictionary.txt" | cut -d\  -f{2}- '.format(start_row, end_row, from_nth_field_onward)
    
#     headers = subprocess.check_output(unix_shell_command, shell=True)
    
#     #headers = subprocess.check_output('awk \'NR>=' + str(start_row) + '&&NR<=' + str(end_row) + '\' "./dictionary.txt" | cut -d\  -f3- ', shell=True)
#     #headers = subprocess.check_output('awk \'NR>=4&&NR<=89\' "./dictionary.txt" | cut -d\  -f3- ', shell=True)
#     # awk \'NR>=4&&NR<=89\' "./dictionary.txt" => take lines between 4 and 89, both incluive
#     #  (NOTE: escape character of "\" before ')
#     # cut -d\  -f3- => delimiter of a single space with escape character of "\" and
#     #  taking in the 3rd field onwards until end of the line
#     # This returns byte string e.g., b'Customer Subtype see L0\nNumber of...'

#     # Alternative to 'subprocess.check_output' is as follows:
#     # import os
#     # os.system("command")

#     header_list = "".join(map(chr, headers)).split('\n')
#     # "".join(map(chr, headers)) => convert bytes to a string
#     # .split('\n') => put the produced string into a list delimited by a line feed

#     header_list.pop()
#     # Unfortuantely this leaves a zero-string list item at the very end i.e., (''), so take it out

#     return header_list

In [4]:
def collect_data(keyword, first_item_number, from_nth_field):
    """
    RETURN: A list of items in data file
    first_item_number: Either 0 or 1, by which a first item is numbered
    from_nth_field: The number on and which field to the end of line to extract, delimited by a single space ' '
    """

    path_and_file_name_of_dictionary = "./dictionary.txt" # In relation to this ipynb file
    item_list = []
    
    section_found = False
    item_found = False
    end_of_info = False

    # Without "encoding="ISO-8859-1", non-printbale character spits "UnicodeDecodeError: 'utf-8' codec can't decode..."
    with open (path_and_file_name_of_dictionary, 'rt', encoding="ISO-8859-1") as myfile:
        for a_line in myfile:
            if (not end_of_info):
                if (not section_found) and (a_line[:len(keyword)] == keyword):
                    section_found = True
                elif section_found and (a_line[0]== str(first_item_number) or item_found):
                    if a_line == '\n':
                        end_of_info = True
                    else:
                        item_name = ''
                        field_list = a_line.split()

                        for idx in range(from_nth_field - 1, len(field_list)):
                            item_name = item_name + ' ' + field_list[idx]

                        item_list.append(item_name[1:len(item_name)])
                        item_found = True
            else:
                return item_list
    return item_list # When reaching end of file, this line gets executed for 'L4'

In [5]:
def fetch_list_item(nd_array, keyword, from_nth_index = 0):
    """
    RETURN: A tuple of matched item AND index number 
    Fetch column name according to the passed-in 'keyword'
    Perform "exact" search to see if string match AT the end of string ONLY
    """
    
    for index, item in enumerate(nd_array):
        if index >= from_nth_index:
            if item[-len(keyword):] == keyword:
                return index, item
    return None

In [6]:
def remove_duplicate(df_series, dictionary, offset):
    """
    RETURN: A list without a duplicate
    df_series: A DataFrame Series, i.e., one-column DataFrame
    dictionary: A list of items in the look-up dictionary
    offset: Either 0 or 1, by which to offset raw data numbers as the dicionary is always 0-based
    """
    
    # Create a ndarray from a DataFrame column
    nd_array_data = df_series.to_numpy()
    
    # DEBUG np.savetxt(r"./test_start.txt", nd_array_data)
    
    duplicate_items = []
    
    for index, item in enumerate(dictionary):
        if dictionary.count(item) > 1:
            res =  fetch_list_item(dictionary, item, index+1)
            if res is not None:
            # Locate the index of the OTHER duplicate, to be kept and aligned, from the beginning of the list
                duplicate_num, _ = res

                duplicate_items.append([index, duplicate_num])
    
    # Finally take out the duplicates        
    for dup in duplicate_items:
        dictionary.pop(dup[0]) 
        
        # The subsequent items of the found duplicate must be pushed forward by subtracting 1, to have it asligned with dictionary.txt
        nd_array_data = np.where(nd_array_data>dup[0], nd_array_data - 1, nd_array_data)
        
        # Now replace the duplicate index with the OTHER index of its identical entry
        nd_array_data[np.where(nd_array_data==dup[0])] = dup[1]

    # Adjust raw data numbers where its corresponding column/field in the dectionary list has 1-based order
    nd_array_data = nd_array_data - offset
    
    return dictionary, nd_array_data

In [7]:
def change_column_type_from_int64_to_category():
    """
    Format DataFrame by replacing 'pure' indices in dictionary.txt with meaningful descriptions
    """

    dictionary_label_prefix = 'L'
    
    data_tables = [[0, 1, 2], 
                     [1, 1, 2], 
                     [2, 1, 2], 
                     [3, 0, 2], 
                     [4, 0, 2]]
    # 1st element: A number - prefixed with 'L' - whose table in the dictionary.txt describes further e.g., L0, L1, and L2
    # 2nd element: N-based index in the dictionary.txt. Where it's 1 
    #              we subtract 1 from the original data to make it zero(0)-based, so as to suit indexes of category type
    # 3rd element: The number of n-th field in each line to be taken    
    
    for i in data_tables:
        res = fetch_list_item(list_of_column_names,
                              dictionary_label_prefix + str(i[0]),
                              0)
        if res is not None:
            index, item = res
            
            corrected_dictionary, new_values = remove_duplicate(df_raw[item], 
                                                                collect_data(dictionary_label_prefix + str(i[0]), i[1], i[2]),
                                                                i[1])

            df_raw[item] = new_values

            df_raw[item] = pd.CategoricalIndex(df_raw[item].map(dict(enumerate(corrected_dictionary))),
                                                 ordered=True, 
                                                 categories=corrected_dictionary)

In [8]:
column_names = [["DATA DICTIONARY", 1, 3]]
list_of_column_names = collect_data(str(column_names[0][0]), column_names[0][1], column_names[0][2])

df_raw.columns = list_of_column_names

In [9]:
change_column_type_from_int64_to_category()

In [15]:
df_raw.to_feather('formatted_raw_data')

Customer Subtype see L0  Number of houses 1  10  \
0                     Lower class large families                        1   
1                      Mixed small town dwellers                        1   
2                      Mixed small town dwellers                        1   
3                      Modern, complete families                        1   
4                             Large family farms                        1   
5                               Young and rising                        1   
6                        Large religous families                        2   
7                     Lower class large families                        1   
8                     Lower class large families                        1   
9                                Family starters                        2   
10                                 Stable family                        1   
11                     Modern, complete families                        1   
12                    Lower class large families                        1   
13                                  Mixed rurals                        1   
14                              Young and rising                        1   
15                    Lower class large families                        1   
16                          Traditional families                        1   
17                      Mixed apartment dwellers                        2   
18                     Young all american family                        1   
19                          Low income catholics                        1   
20                    Lower class large families                        1   
21                    Lower class large families                        2   
22                     Young all american family                        1   
23                  Large family, employed child                        2   
24                     Young all american family                        2   
25                    Lower class large families                        1   
26                     Mixed small town dwellers                        1   
27                            Large family farms                        1   
28                          Low income catholics                        1   
29                    Lower class large families                        2   
30                           Young, low educated                        2   
31                              Young and rising                        1   
32                    Lower class large families                        1   
33                          Traditional families                        1   
34                     Young all american family                        2   
35                         Middle class families                        1   
36               Dinki's (double income no kids)                        1   
37                                  Mixed rurals                        1   
38                       Large religous families                        1   
39                    Lower class large families                        2   
40                           Young, low educated                        1   
41                               Family starters                        1   
42                         Middle class families                        1   
43                    Lower class large families                        1   
44                           High status seniors                        1   
45                          Traditional families                        1   
46    Couples with teens 'Married with children'                        1   
47                          Traditional families                        1   
48                       Large religous families                        1   
49                    Lower class large families                        2   
50                    Lower class large families                        1   
51                   

# Data Exploring

In [ ]:
df_raw = pd.read_feather('formatted_raw_data')

In [11]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split

df_test = pd.read_csv(r"./ticeval2000.txt", sep='\t', header=None, low_memory=False)

In [12]:
df_raw.shape, df_test.shape
# print("# of raw records = {0}\n# of rows in testing set = {1}".format(len(df_raw), len(df_test)))

((5822, 86), (4000, 85))

In [13]:
df_target = pd.read_csv(r"./tictgts2000.txt", sep='\t', header=None, low_memory=False)

Good benchmark to extract validation set out of training set is 20% according to Fast.ai's Jeremy Howard. Also take a look at this descerning article (https://www.fast.ai/2017/11/13/validation-sets/).

The sample is NOT a timeseries data and thus cross-validation can be a good candidate as well as out-of-bag hyperparameter in Random Forest.

In [23]:
# https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.train_test_split.html

# Separate into 2 DataFarmes:
#  1. Target/Dependent value (Attribute 86, "CARAVAN:Number of mobile home policies") and 
#  2. Features

# Tuple is zero-based, but columns is one-based
col_idx = df_raw.shape[1]-1

df_target = df_raw.iloc[:, col_idx]
df_features = df_raw.drop(df_raw.columns[col_idx], axis='columns')

# Use train_test_split to create train and validation set instead of test set, which we already have
# Random seed is of course '42' due to 'The Hitchhiker's Guide to the Galaxy'!
X_train, X_valid, y_train, y_valid = train_test_split(df_features, df_target, train_size=0.8, random_state=42)

X_train.shape, X_valid.shape, y_train.shape, y_valid.shape

/home/to/miniconda3/envs/caravan/lib/python3.6/site-packages/sklearn/model_selection/_split.py:2179: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


((4657, 85), (1165, 85), (4657,), (1165,))

In [28]:
X_train['Customer Subtype see L0'].cat.codes.head()

252     14
350     39
2836    31
2864    35
457     36
dtype: int8

In [24]:
m = RandomForestRegressor(n_jobs=-1)
m.fit(X_train, y_train)
m.score

/home/to/miniconda3/envs/caravan/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)


ValueError: could not convert string to float: 'Students in apartments'

In [20]:
df_raw.shape[1]

86